In [ ]:
import tokre
import tinymodel
from tinymodel import TinyModel
from datasets import load_dataset
from torch.utils.data import DataLoader
import torch

DEVICE = 'mps'
torch.set_grad_enabled(False)

lm = TinyModel().to(torch.float16).to(DEVICE)

tokre.setup(tokenizer=tinymodel.tokenizer, workspace='workspace')

ds = load_dataset('noanabeshima/TinyModelTokIds', split='train[:4%]')


(pid=90345) Calling ray.init() again after it has already been called.
(ParallelModule pid=90345) /Users/noanabeshima/.miniconda/envs/tokre/lib/python3.12/site-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue o

In [ ]:
from tqdm import tqdm
import numpy as np

dataloader = DataLoader(ds, batch_size=50)

get_acts = lm['A1']

all_acts, all_toks = [], []
for batch in tqdm(dataloader):
    tok_ids = torch.stack(batch['tok_ids'], dim=-1).to(lm.device)
    acts = get_acts(tok_ids, indices=slice(0, 2_000))
    all_acts.append(acts.cpu())
    all_toks.append(tok_ids.cpu())

acts = torch.cat(all_acts, dim=0)
toks = torch.cat(all_toks, dim=0)

acts = acts/acts.max(dim=-1, keepdim=True).values
toks = tinymodel.raw_toks[toks]

In [ ]:
FEAT = 34

feat_acts = acts[...,FEAT]

feat_mask = (feat_acts.max(dim=-1).values > 0)
feat_acts = feat_acts[feat_mask]
feat_toks = toks[feat_mask]


In [ ]:
import pysvelte


pysvelte.WeightedDocs(acts=feat_acts.float().tolist(), docs=feat_toks.tolist())

In [ ]:
tor

In [24]:
ds = load_dataset('noanabeshima/TinyStoriesV2', split='validation')

In [26]:
words = tokre.get_word_counts(ds)

 41%|████▏     | 11418/27629 [02:03<02:48, 95.96it/s] 

(autoscaler +13m1s) Tip: use `ray status` to view detailed cluster status. To disable these messages, set RAY_SCHEDULER_EVENTS=0.
(autoscaler +13m1s) Warning: The following resource request cannot be scheduled right now: {'CPU': 1.0}. This is likely due to all cluster resources being claimed by actors. Consider creating fewer actors or adding more nodes to this Ray cluster.
(autoscaler +13m36s) Warning: The following resource request cannot be scheduled right now: {'CPU': 1.0}. This is likely due to all cluster resources being claimed by actors. Consider creating fewer actors or adding more nodes to this Ray cluster.
(autoscaler +14m12s) Warning: The following resource request cannot be scheduled right now: {'CPU': 1.0}. This is likely due to all cluster resources being claimed by actors. Consider creating fewer actors or adding more nodes to this Ray cluster.
(autoscaler +14m47s) Warning: The following resource request cannot be scheduled right now: {'CPU': 1.0}. This is likely due to

Error tokenizing document: argmin(): Expected reduction dim 1 to have non-zero size.


100%|██████████| 27629/27629 [05:00<00:00, 91.96it/s] 


In [28]:
word_counts = words

27629

In [35]:
words = [word[0] for word in word_counts if '[UNK]' not in word[0]]

In [37]:
tokre.save_literal_set('words', 'Words extracted from validation set of TinyStories V2', literals=words, vary_leading_space=True, vary_capitalization=True, strip_and_lowercase=False)

In [51]:
N_SAMPLES = 1000
synth = tokre.SynthFeat('''[literal_set `words` prefix=True]''')

test_acts = acts[...,FEAT][:N_SAMPLES]
test_toks = toks[:N_SAMPLES]


synth_mask = synth.get_mask(test_toks)


VisitError: Error trying to process rule "macro":

LiteralSet.__init__() got an unexpected keyword argument 'prefix'

In [43]:
(test_acts*synth_mask).var()/test_acts.var()

tensor(0.9421)

In [46]:
# pysvelte.WeightedDocs(acts=(synth_mask).tolist(), docs=test_toks.tolist())

In [47]:
pysvelte.WeightedDocs(acts=(test_acts*(1-synth_mask)).tolist(), docs=test_toks.tolist())